# Todo list: 
<li> Find a way to "trigger" messege to kafka (May not need to store in hdfs anymore-> contr)</li>
<li> Push to github </li>

In [ ]:
!pip install --user kafka-python

In [ ]:
from kafka import KafkaConsumer
import json
try:
    print('Welcome to parse engine')
    consumer = KafkaConsumer('email_alert',
                             bootstrap_servers='188.185.79.229:9092',
#To subscribe since the first message that has been produced to kafka producer
                             auto_offset_reset='earliest',
                             enable_auto_commit=False,
                             group_id=None,
                             value_deserializer=lambda m: json.loads(m)
                            )
    for message in consumer:
        print(message.value['subject'])
except Exception as e:
    print(e)
    # Logs the error appropriately.
    pass

In [ ]:
!wget http://central.maven.org/maven2/org/apache/spark/spark-sql-kafka-0-10_2.11/2.4.1/spark-sql-kafka-0-10_2.11-2.4.1.jar

In [ ]:
!wget http://central.maven.org/maven2/org/apache/spark/spark-streaming-kafka-0-8-assembly_2.10/2.0.0-preview/spark-streaming-kafka-0-8-assembly_2.10-2.0.0-preview.jar

In [1]:
from pyspark.sql.functions import *
from pyspark.sql.types import *
from datetime import datetime
emailSchema = StructType() \
        .add("subject", StringType()) \
        .add("body", StringType())

# Group the data by window and subject and compute the count of each group

<li>The engine will maintain state and allow late data to be update the state until (max event time seen by the engine - late threshold > 1 Month). In other words, late data within the threshold will be aggregated, but data later than the threshold will be dropped.</li> 
<li>Count subject within 1 day windows, updating every 40 minutes</li>

In [14]:
from pyspark.sql.types import StructType
import json
# Subscribe to 1 topic
data = spark.readStream.format("kafka")\
.option("kafka.bootstrap.servers", "188.185.79.229:9092")\
.option("subscribe","email_alert")\
.option("startingOffsets", "earliest") \
.load()\
.select(
    from_json(col("value").cast("string"), emailSchema).getField("subject").alias("subject"),
    col("timestamp").alias("timestamp"))\
.withWatermark("timestamp", "1 month")\
.groupBy(window('timestamp', "30 day", "40 minutes"),"subject")\
.agg(count("subject"))\

# .selectExpr("CAST(key AS STRING)", "CAST(value AS STRING)") \
#   .writeStream \
#   .format("kafka") \
#   .option("kafka.bootstrap.servers", "host1:port1,host2:port2") \
#   .option("topic", "topic1") \
#   .trigger(continuous="1 second") \ 
data.printSchema()

root
 |-- window: struct (nullable = true)
 |    |-- start: timestamp (nullable = true)
 |    |-- end: timestamp (nullable = true)
 |-- subject: string (nullable = true)
 |-- count(subject): long (nullable = false)



In [15]:
flow = data.writeStream.queryName("email").outputMode("Append").format("memory").start()

In [12]:
data.isStreaming

True

In [11]:
flow.stop()

In [13]:
spark.streams.active

[]

In [208]:
flow.lastProgress

{'id': '9615b57b-cdba-47f4-906d-e9b7972db3f0',
 'runId': '14a8f242-639f-464b-ab82-51ab64811cdc',
 'name': 'subject',
 'timestamp': '2019-06-07T09:08:48.166Z',
 'batchId': 2,
 'numInputRows': 0,
 'inputRowsPerSecond': 0.0,
 'processedRowsPerSecond': 0.0,
 'durationMs': {'getEndOffset': 0, 'setOffsetRange': 2, 'triggerExecution': 2},
 'eventTime': {'watermark': '2018-05-28T08:30:02.000Z'},
 'stateOperators': [{'numRowsTotal': 75,
   'numRowsUpdated': 0,
   'memoryUsedBytes': 100719,
   'customMetrics': {'loadedMapCacheHitCount': 400,
    'loadedMapCacheMissCount': 0,
    'stateOnCurrentVersionSizeBytes': 35999}}],
 'sources': [{'description': 'KafkaV2[Subscribe[email_alert]]',
   'startOffset': {'email_alert': {'0': 1152}},
   'endOffset': {'email_alert': {'0': 1152}},
   'numInputRows': 0,
   'inputRowsPerSecond': 0.0,
   'processedRowsPerSecond': 0.0}],
 'sink': {'description': 'MemorySink'}}

In [18]:
alerts = spark.sql("select * from email")
alerts.show()

+------+-------+--------------+
|window|subject|count(subject)|
+------+-------+--------------+
+------+-------+--------------+



In [207]:
alerts = spark.sql("select * from emailCount")

True

In [331]:
window?

In [ ]:
# dfraw.groupby(window(dfraw.timeColumn, "5 minutes"))

In [ ]:
# emailCounts = streaming.groupBy("subject").count()

In [163]:
# flow=df.writeStream.queryName("email")\
#   .outputMode("update")\
#   .format("memory")\
#   .start()


In [23]:
# spark.sql("select * from email").show()
alerts = spark.sql("select * from email")
alerts.head()

Row(jsontostructs(CAST(value AS STRING))=Row(subject='Problem POPDB Xrootd File2DS CRON', body='check log in /opt/CMSDataPopularity/xrootd/log\r\n'))

In [313]:
# alertLate=alerts.withWatermark("time", "24 hours").groupBy(["timestamp"]).count()
# alertLate.head()


pyspark.sql.streaming.StreamingQuery

In [286]:
from ast import literal_eval
rddAlertsRdd = alerts.rdd.map(lambda alert: literal_eval(alert['value']))

In [334]:
rddAlertsRdd

PythonRDD[163] at collect at <ipython-input-287-d7e0b4c14d8a>:1

In [287]:
rddAlerts = rddAlertsRdd.collect()

In [333]:
rddAlerts

[{'subject': 'Problem POPDB Xrootd File2DS CRON',
  'body': 'check log in /opt/CMSDataPopularity/xrootd/log\r\n'},
 {'subject': 'Problem POPDB Xrootd File2DS CRON',
  'body': 'check log in /opt/CMSDataPopularity/xrootd/log\r\n'},
 {'subject': 'Problem POPDB Xrootd File2DS CRON',
  'body': 'check log in /opt/CMSDataPopularity/xrootd/log\r\n'},
 {'subject': 'Cron <root@vocms041> cd /opt/CMSDataPopularity/xrootd; python2.6 lib/checkMViews.py',
  'body': 'WARNING: MView MV_XRD_STAT1 not refreshed since 2019-03-25 17:41:12\r\nWARNING: MView MV_XRD_DS_STAT1_AGGR1 not refreshed since 2019-03-25 20:34:48\r\nWARNING: MView MV_XRD_STAT2 not refreshed since 2019-04-02 13:08:20\r\n'},
 {'subject': 'Problem POPDB Xrootd File2DS CRON',
  'body': 'check log in /opt/CMSDataPopularity/xrootd/log\r\n'},
 {'subject': 'Problem POPDB Xrootd File2DS CRON',
  'body': 'check log in /opt/CMSDataPopularity/xrootd/log\r\n'},
 {'subject': 'PopDB cronJob of cron_2019-04-05_04-30-06.log',
  'body': '-----> hostname

In [292]:
pdAlerts = alerts.toPandas()

In [293]:
pdAlertsSeries = pdAlerts['value'].map(literal_eval)

In [294]:
import pandas
pdAlertsDf = pandas.DataFrame(list(pdAlertsSeries))
pdAlertsDf.index = pdAlerts['timestamp']

In [295]:
pdAlertsDf.head()

body  \
timestamp                                                                
2019-06-04 00:00:04  check log in /opt/CMSDataPopularity/xrootd/log...   
2019-06-04 10:30:02  check log in /opt/CMSDataPopularity/xrootd/log...   
2019-04-05 02:20:04  check log in /opt/CMSDataPopularity/xrootd/log...   
2019-04-05 03:00:03  WARNING: MView MV_XRD_STAT1 not refreshed sinc...   
2019-04-05 04:40:02  check log in /opt/CMSDataPopularity/xrootd/log...   

                                                               subject  
timestamp                                                               
2019-06-04 00:00:04                  Problem POPDB Xrootd File2DS CRON  
2019-06-04 10:30:02                  Problem POPDB Xrootd File2DS CRON  
2019-04-05 02:20:04                  Problem POPDB Xrootd File2DS CRON  
2019-04-05 03:00:03  Cron <root@vocms041> cd /opt/CMSDataPopularity...  
2019-04-05 04:40:02                  Problem POPDB Xrootd File2DS CRON

In [327]:
import datetime
aggSubject=pdAlertsDf.groupby(['subject',pandas.Grouper(freq='1M')]).count()
aggSubject

body
subject                                            timestamp       
CRITICAL: too many xrootd-cms-eos-popularity me... 2019-04-30     3
Cron <root@vocms041> cd /opt/CMSDataPopularity/... 2019-04-30    18
                                                   2019-05-31    14
Cron alert CMS Popularity                          2019-05-31    11
Notification: Restart simplevisor at vocms042.c... 2019-04-30    15
Notification: Restart simplevisor at vocms043.c... 2019-04-30    14
Notification: Stop simplevisor at vocms042.cern... 2019-04-30    15
Notification: Stop simplevisor at vocms043.cern... 2019-04-30    12
Notification: Stop simplevisor at vocms043.cern... 2019-04-30     2
Notification: Stop two insertion agents at vocm... 2019-04-30     2
Notification: Stop two insertion agents at vocm... 2019-04-30     2
OK: xrootd-cms-eos-popularity messages stored o... 2019-04-30     4
                                                   2019-05-31     1
PopDB cronJob of cron_2019-04-05_04-30-06.log      2019-04-30     1
PopDB cronJob of cron_2019-04-06_04-30-05.log      2019-04-30     1
PopDB cronJob of cron_2019-04-07_04-30-04.log      2019-04-30     1
PopDB cronJob of cron_2019-04-08_04-30-05.log      2019-04-30     1
PopDB cronJob of cron_2019-04-09_04-30-04.log      2019-04-30     1
PopDB cronJob of cron_2019-04-10_04-30-04.log      2019-04-30     1
PopDB cronJob of cron_2019-04-11_04-30-04.log      2019-04-30     1
PopDB cronJob of cron_2019-04-12_04-30-04.log      2019-04-30     1
PopDB cronJob of cron_2019-04-13_04-30-01.log      2019-04-30     1
PopDB cronJob of cron_2019-04-14_04-30-01.log      2019-04-30     1
PopDB cronJob of cron_2019-04-15_04-30-05.log      2019-04-30     1
PopDB cronJob of cron_2019-04-16_04-30-05.log      2019-04-30     1
PopDB cronJob of cron_2019-04-17_04-30-03.log      2019-04-30     1
PopDB cronJob of cron_2019-04-18_04-30-02.log      2019-04-30     1
PopDB cronJob of cron_2019-04-19_04-30-04.log      2019-04-30     1
PopDB cronJob of cron_2019-04-20_04-30-08.log      2019-04-30     1
PopDB cronJob of cron_2019-04-21_04-30-05.log      2019-04-30     1
...                                                             ...
PopDB cronJob of cron_2019-04-25_04-30-04.log      2019-04-30     1
PopDB cronJob of cron_2019-04-26_04-30-03.log      2019-04-30     1
PopDB cronJob of cron_2019-04-27_04-30-04.log      2019-04-30     1
PopDB cronJob of cron_2019-04-28_04-30-02.log      2019-04-30     1
PopDB cronJob of cron_2019-04-29_04-30-01.log      2019-04-30     1
PopDB cronJob of cron_2019-04-30_04-30-06.log      2019-04-30     1
PopDB cronJob of cron_2019-05-01_04-30-02.log      2019-05-31     1
PopDB cronJob of cron_2019-05-02_04-30-01.log      2019-05-31     1
PopDB cronJob of cron_2019-05-03_04-30-02.log      2019-05-31     1
PopDB cronJob of cron_2019-05-04_04-30-01.log      2019-05-31     1
PopDB cronJob of cron_2019-05-05_04-30-04.log      2019-05-31     1
PopDB cronJob of cron_2019-05-06_04-30-04.log      2019-05-31     1
PopDB cronJob of cron_2019-05-07_04-30-04.log      2019-05-31     1
PopDB cronJob of cron_2019-05-08_04-30-03.log      2019-05-31     1
PopDB cronJob of cron_2019-05-09_04-30-02.log      2019-05-31     1
PopDB cronJob of cron_2019-05-10_04-30-06.log      2019-05-31     1
PopDB cronJob of cron_2019-05-11_04-30-02.log      2019-05-31     1
PopDB cronJob of cron_2019-05-12_04-30-04.log      2019-05-31     1
PopDB cronJob of cron_2019-05-13_04-30-01.log      2019-05-31     1
Problem POPDB Xrootd File2DS CRON                  2019-04-30   199
                                                   2019-05-31   170
                                                   2019-06-30    23
The collector xrootd_1 in vocms042.cern.ch was ... 2019-05-31     3
The collector xrootd_1 in vocms043.cern.ch was ... 2019-05-31     3
The collector xrootd_2 in vocms042.cern.ch was ... 2019-04-30     1
                                                   2019-05-31     3
The collector xrootd_2 in vocms043.cern.ch was ... 

In [310]:
type(aggSubject)

pandas.core.frame.DataFrame

In [322]:
arr=pdAlertsDf.index.get_loc('2019-06-04')
arr
for i in arr:
    print(pdAlertsDf.iloc[i])

body       check log in /opt/CMSDataPopularity/xrootd/log...
subject                    Problem POPDB Xrootd File2DS CRON
Name: 2019-06-04 00:00:04, dtype: object
body       check log in /opt/CMSDataPopularity/xrootd/log...
subject                    Problem POPDB Xrootd File2DS CRON
Name: 2019-06-04 10:30:02, dtype: object
body       check log in /opt/CMSDataPopularity/xrootd/log...
subject                    Problem POPDB Xrootd File2DS CRON
Name: 2019-06-04 00:00:04, dtype: object
body       check log in /opt/CMSDataPopularity/xrootd/log...
subject                    Problem POPDB Xrootd File2DS CRON
Name: 2019-06-04 10:30:02, dtype: object
